In Deus Ex: Human Revolution when you get to Hengsha you eventually break into a dude's apartment, and find a room with a load of post-its including this one which features what appears to be a message in binary:

![hengsha post-it](https://notes.mclemon.net/binary-post-it.jpg)

In [2]:
# there are two potential interpretations of the post-it 
# because the final line has a little mark that could be
# nothing or it could be a 1
raw_messages = [
    """
        1001001111
        00101100
        1001110
        111010101
        101110011
    """,
    
    """
        1001001111
        00101100
        1001110
        111010101
        1011101011
    """
]

def message_lines(message_str):
    return [line.strip() for line in message_str.split()]


def try_format(formatter):
    for raw_message in raw_messages:
        for output in formatter(message_lines(raw_message)):
            print(output)
        print("---------------")

# let's test this out for starters, return the raw lines as-is
def identity_formatter(lines):
    for line in lines:
        yield line
        
try_format(identity_formatter)

1001001111
00101100
1001110
111010101
101110011
---------------
1001001111
00101100
1001110
111010101
1011101011
---------------


In [52]:
# let's start just treating each line as a plain unsigned int
def plain_int(lines):
    for line in lines:
        yield int(line, 2)
        

try_format(plain_int)

591
44
78
469
371
---------------
591
44
78
469
747
---------------


In [53]:
# let's try just chopping off any characters after 7 bits 
# (since that's the shortest line length) and treat that as
# a char
def truncate_to_7_bytes(lines):
    for line in lines:
        yield chr(int(line[:7], 2))
        
try_format(truncate_to_7_bytes)        

I

N
u
\
---------------
I

N
u
]
---------------


In [54]:
# same as above but 8?
def truncate_to_8_bytes(lines):
    for line in lines:
        yield chr(int(line[:8], 2))
        
try_format(truncate_to_8_bytes)        


,
N
ê
¹
---------------

,
N
ê
º
---------------


In [55]:
# ok let's smash it all together, munch through them 7-bits
# at a time and see what happens
def seven_bit_stream(lines):
    stream = "".join(lines)
    
    while len(stream) >= 7:
        byte = stream[:7]
        yield chr(int(byte, 2))
        stream = stream[7:]
        
    # fuck it, yield whatever's left, it'll be unprintable
    yield chr(int(stream, 2))

try_format(seven_bit_stream)

I
r
d
w
+
9

---------------
I
r
d
w
+
:

---------------


In [56]:
# as above but 8 instead of 7
def eight_bit_stream(lines):
    stream = "".join(lines)
    
    while len(stream) >= 8:
        byte = stream[:8]
        yield chr(int(byte, 2))
        stream = stream[8:]
        
    # fuck it, yield whatever's left, it'll be unprintable
    yield chr(int(stream, 2))

try_format(eight_bit_stream)


Ë
'
u
n

---------------

Ë
'
u
n

---------------


In [4]:
# maybe there's a header of sorts
def skip_some_bits(lines):
    entire_stream = "".join(lines)
    
    for n in range(len(entire_stream)-8):
        message = []
        stream = entire_stream[n:]
        while len(stream) >= 8:
            byte = stream[:8]
            message.append(chr(int(byte, 2)))
            stream = stream[8:]
        
        yield n, "".join(message)
    
        
    
try_format(skip_some_bits)

(0, "\x93Ë'un")
(1, "'\x96NêÜ")
(2, 'O,\x9dÕ¹')
(3, '\x9eY;«s')
(4, '<²wV')
(5, 'ydî\xad')
(6, 'òÉÝ[')
(7, 'å\x93º·')
(8, "Ë'un")
(9, '\x96NêÜ')
(10, ',\x9dÕ¹')
(11, 'Y;«s')
(12, '²wV')
(13, 'dî\xad')
(14, 'ÉÝ[')
(15, '\x93º·')
(16, "'un")
(17, 'NêÜ')
(18, '\x9dÕ¹')
(19, ';«s')
(20, 'wV')
(21, 'î\xad')
(22, 'Ý[')
(23, 'º·')
(24, 'un')
(25, 'êÜ')
(26, 'Õ¹')
(27, '«s')
(28, 'V')
(29, '\xad')
(30, '[')
(31, '·')
(32, 'n')
(33, 'Ü')
(34, '¹')
---------------
(0, "\x93Ë'un")
(1, "'\x96NêÝ")
(2, 'O,\x9dÕº')
(3, '\x9eY;«u')
(4, '<²wVë')
(5, 'ydî\xad')
(6, 'òÉÝ[')
(7, 'å\x93º·')
(8, "Ë'un")
(9, '\x96NêÝ')
(10, ',\x9dÕº')
(11, 'Y;«u')
(12, '²wVë')
(13, 'dî\xad')
(14, 'ÉÝ[')
(15, '\x93º·')
(16, "'un")
(17, 'NêÝ')
(18, '\x9dÕº')
(19, ';«u')
(20, 'wVë')
(21, 'î\xad')
(22, 'Ý[')
(23, 'º·')
(24, 'un')
(25, 'êÝ')
(26, 'Õº')
(27, '«u')
(28, 'Vë')
(29, '\xad')
(30, '[')
(31, '·')
(32, 'n')
(33, 'Ý')
(34, 'º')
(35, 'u')
---------------


In [58]:
# ok this is nonsense and a waste of time